In [1]:
#!/home/kddmer/.pyenv/versions/env3/bin/python
# -*- coding: utf-8 -*-

import sys
import os
import numpy as np

%matplotlib inline
from matplotlib import pyplot as plt
import cv2
sys.path.append("/home/kddmer/models/imgp/auto_wmr")
import estimate_watermark as ew
import preprocess as pp

# 预处理图像为500*500
# pp.preprocess('images/company_raw', 'images/company_proc')


In [2]:
# 识别水印位置
gx, gy, gxlist, gylist = ew.estimate_watermark('images/fotolia_proc')
est = ew.poisson_reconstruct(gx, gy)
cropped_gx, cropped_gy = ew.crop_watermark(gx, gy)
W_m = ew.poisson_reconstruct(cropped_gx, cropped_gy)


    Computing gradients.
    Computing median gradients.


In [8]:
W_mod = np.sqrt(np.square(gx) + np.square(gy))
W_mod = ew.PlotImage(W_mod)
plt.imshow(W_mod)

In [7]:
plt.imshow(ew.PlotImage(gy))
plt.show()

In [11]:
# random photo
img = cv2.imread('images/fotolia_proc/fotolia_4282406.jpg')
im, start, end = ew.watermark_detector(img, cropped_gx, cropped_gy)

plt.figure(figsize=(12, 12), dpi= 80, facecolor='w', edgecolor='k')
plt.imshow(im)
plt.show()

In [79]:
num_images = len(gxlist)

import watermark_reconstruct as wr
J, img_paths = wr.get_cropped_images('images/fotolia_proc', num_images, start, end, cropped_gx.shape)
print(img_paths)

['images/fotolia_proc/fotolia_4414002.jpg', 'images/fotolia_proc/fotolia_3513973.jpg', 'images/fotolia_proc/fotolia_4282406.jpg', 'images/fotolia_proc/fotolia_2438493.jpg', 'images/fotolia_proc/fotolia_40674271.jpg', 'images/fotolia_proc/fotolia_52607811.jpg', 'images/fotolia_proc/fotolia_26734091.jpg', 'images/fotolia_proc/fotolia_13257157.jpg', 'images/fotolia_proc/fotolia_50960166.jpg', 'images/fotolia_proc/fotolia_31531037.jpg', 'images/fotolia_proc/fotolia_31515464.jpg', 'images/fotolia_proc/fotolia_8957978.jpg', 'images/fotolia_proc/fotolia_3279225.jpg', 'images/fotolia_proc/fotolia_3896507.jpg', 'images/fotolia_proc/fotolia_39602580.jpg', 'images/fotolia_proc/fotolia_592458.jpg', 'images/fotolia_proc/fotolia_38287157.jpg', 'images/fotolia_proc/fotolia_688089.jpg', 'images/fotolia_proc/fotolia_31736288.jpg', 'images/fotolia_proc/fotolia_2584384.jpg', 'images/fotolia_proc/fotolia_1011792.jpg', 'images/fotolia_proc/fotolia_5644281.jpg', 'images/fotolia_proc/fotolia_31324185.jpg', '

In [8]:

# Wm = (255 * ew.PlotImage(W_m))
Wm = W_m - W_m.min()

# get threshold of W_m for alpha matte estimate
alph_est = wr.estimate_normalized_alpha(J, Wm, num_images)
alph = np.stack([alph_est, alph_est, alph_est], axis=2)
C, est_Ik = wr.estimate_blend_factor(J, Wm, alph)

alpha = alph.copy()
for i in range(3):
	alpha[:,:,i] = C[i] * alpha[:, :, i]

Wm = Wm + alpha * est_Ik

Estimating normalized alpha using 48 images.
0.2779031814810184
0.25554972698205325
0.24602142248159


In [10]:
import copy
W = copy.deepcopy(Wm)
for i in range(3): 
	W[:,:,i] /= C[i]
    
Jt = J[: 25]

In [38]:
img = cv2.imread('images/fotolia_processed/fotolia_4414002.jpg')
plt.figure(figsize=(12, 12), dpi= 80, facecolor='w', edgecolor='k')
plt.imshow(img)

In [53]:
img2 = copy.deepcopy(img)
print(start, end)
ii = 0
for i in range(229, 229+39):
    jj = 0
    for j in range(164, 164+172):
        img2[i][j] = Ik[0][ii][jj]
        jj +=1
    ii +=1
    

(229, 164) (39, 172)


In [54]:
plt.figure(figsize=(12, 12), dpi= 80, facecolor='w', edgecolor='k')
plt.imshow(img2)
cv2.imwrite(os.sep.join([dest_folder, file]), img2)

In [72]:
proc_folder = 'images/fotolia_proc'
fpath, dir, files = list(os.walk(proc_folder))[0]
path = (os.sep.join([os.path.abspath(fpath), files[0]]))
print(path)

/home/kddmer/models/imgp/auto_wmr/images/fotolia_proc/fotolia_4414002.jpg


In [55]:
cv2.imwrite('images/fotolia_processed/fotolia_4414002_wmr.jpg',img2)

True

In [11]:

print(Ik.shape)
plt.imshow(ew.PlotImage(Ik[0]))

# now we have the values of alpha, Wm, J
# Solve for all images
Wk, Ik, W, alpha1 = wr.solve_images(Jt, W_m, alpha, W)

------------------------------------
Iteration: 0
Step 1


0


1


2


3


...

21


22


23


24
Step 2


Step 3


In [13]:
W_m_threshold = (255 * ew.PlotImage(np.average(W_m, axis=2))).astype(np.uint8)
ret, thr = cv2.threshold(W_m_threshold, 127, 255, cv2.THRESH_BINARY)

In [18]:
print(Ik.shape)

(25, 39, 172, 3)


In [20]:
plt.imshow(ew.PlotImage(Ik[0]))

In [22]:
plt.imshow(ew.PlotImage(Ik[0]))

In [74]:
file = 'fotolia_4414002.jpg'
filewmr = file.split('.')[0] + '_wmr.' + file.split('.')[1]
print(filewmr)

fotolia_4414002_wmr.jpg


In [81]:
start/10

TypeError: unsupported operand type(s) for /: 'tuple' and 'int'